In [28]:
import pythainlp
import numpy as np
import pandas as pd
import snapy
import mmh3
import time

In [43]:
from snapy import MinHash, LSH
from pythainlp import sent_tokenize, word_tokenize
from datasketch import MinHash, MinHashLSHForest
from pythainlp.util import normalize

In [30]:
# Import CSV file 
df = pd.read_csv('Final_Dataset.csv',skipinitialspace=True)
df.dropna(axis="rows", how="any", inplace=True)

#print(df)
df.head()

Column1                                    restaurant_name  \
0        0  26BraisedBeef (26 ยี่ สับ หลก) ท่าพระจันทร์ - ...   
1        1  26BraisedBeef (26 ยี่ สับ หลก) ท่าพระจันทร์ - ...   
2        3  26BraisedBeef (26 ยี่ สับ หลก) ท่าพระจันทร์ - ...   
3        4  26BraisedBeef (26 ยี่ สับ หลก) ท่าพระจันทร์ - ...   
4        5  26BraisedBeef (26 ยี่ สับ หลก) ท่าพระจันทร์ - ...   

           Reviewer                                           comments  score  \
0   Auditor Journey  🆕ตำนานบทใหม่จากก๋วยเตี๋ยวเนื้อนายโส่ยท่าพระอาท...      4   
1  สาวเหนือเซาะกิ๋น  มาร้านนี้เพราะได้ดูรีวิวในรายการซอส แต่เราไม่ท...      4   
2              Bom+  #MichelinThailand2020 #MichelinPlate2020\n\n26...      4   
3       Bigstargirl  ปกติชอบแวะไปทานร้านก๋วยเตี๋ยวนายโส่ยตรงพระอาทิ...      5   
4            Muummy  ร้านเนื้อทายาทก๋วยเตี๋ยวเนื้อนายโส่ยย่ายถนนพระ...      4   

                   date  Follower  Review  Photos  Length  y  
0  เมื่อ อาทิตย์ที่แล้ว       126     504    3115    1777  1  
1  เมื่อ 3 เดือนที่แล้ว        41     110    1226     393  1  
2          11 ก.ย. 2020     62230    1440   20882    4072  1  
3          22 ต.ค. 2020        42     328    3767    2904  1  
4          19 ต.ค. 2020        18     573    5432     483  0

In [31]:
df.describe()

Column1         score      Follower        Review        Photos  \
count  12113.000000  12113.000000  12113.000000  12113.000000  12113.000000   
mean     151.566334      4.093536   2678.789895    459.215471   4511.765871   
std      123.310362      0.787693   9287.242494    818.238836  11030.441844   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%       51.000000      4.000000      5.000000     28.000000     95.000000   
50%      122.000000      4.000000     22.000000    114.000000    501.000000   
75%      227.000000      5.000000    286.000000    516.000000   3126.000000   
max      594.000000      5.000000  75841.000000   8040.000000  89493.000000   

             Length             y  
count  12113.000000  12113.000000  
mean     554.411376      0.263353  
std      625.923363      0.440471  
min        1.000000      0.000000  
25%      236.000000      0.000000  
50%      362.000000      0.000000  
75%      636.000000      1.000000  
max    11003.000000      1.000000

In [32]:
# delete white space
df['comments'] = df['comments'].str.replace(" ","")


In [33]:
from sklearn.model_selection import train_test_split

df_train, df_test = train_test_split(df, test_size=0.2)
df_train.head()

Column1                                   restaurant_name  \
9422      138        Farm to Table (ฟาร์ม ทู เทเบิ้ล) ไฮด์เอาท์   
7684       59         Bankara Ramen (บังคาระ ราเมง) สุขุมวิท 39   
6582       93  สวนผัก โอ้กะจู๋ (Ohkajhu Organic) Nim City Daily   
4198      313               ทิพย์สมัย ผัดไทยประตูผี (ทิพย์สมัย)   
3198      321        ซ้งเป็ดพะโล้ (Zong Ped Palow) สี่แยกวังหิน   

                   Reviewer  \
9422   Vichida Sangsngapong   
7684  Count von falkenstein   
6582   มิสเตอร์ - ยัดห่าแมน   
4198                 sariie   
3198                      p   

                                               comments  score          date  \
9422  ร้านค่อนข้างหายากอยู่ในตรอกลึกลับรั้วสีขาวประด...      3  23 ส.ค. 2016   
7684  บังคาระราเมงสาขาสุขุมวิท39นี้เป็นร้านราเมงที่ผ...      4  19 พ.ค. 2018   
6582  เพิ่งมาทานร้านนี้ครั้งแรกคนเยอะมากๆโชคดีมาแล้ว...      5  12 ส.ค. 2018   
4198  ยอมรับค่ะว่าเป็นครั้งแรกที่ได้มาทานผัดไทประตูผ...      3  21 ต.ค. 2013   
3198  คนเยอะแต่อาหารมาเร็วและอร่อยราคาไม่แพงมากที่จอ...      4  31 ม.ค. 2014   

      Follower  Review  Photos  Length  y  
9422      2682     124     423     214  0  
7684        17     213     438     427  0  
6582        95    1624   11928     478  0  
4198         8      49     149     332  0  
3198       118     121     303      71  0

In [34]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9690 entries, 9422 to 5742
Data columns (total 11 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Column1          9690 non-null   int64 
 1   restaurant_name  9690 non-null   object
 2   Reviewer         9690 non-null   object
 3   comments         9690 non-null   object
 4   score            9690 non-null   int64 
 5   date             9690 non-null   object
 6   Follower         9690 non-null   int64 
 7   Review           9690 non-null   int64 
 8   Photos           9690 non-null   int64 
 9   Length           9690 non-null   int64 
 10  y                9690 non-null   int64 
dtypes: int64(7), object(4)
memory usage: 908.4+ KB


In [35]:
df_test.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2423 entries, 11617 to 3660
Data columns (total 11 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Column1          2423 non-null   int64 
 1   restaurant_name  2423 non-null   object
 2   Reviewer         2423 non-null   object
 3   comments         2423 non-null   object
 4   score            2423 non-null   int64 
 5   date             2423 non-null   object
 6   Follower         2423 non-null   int64 
 7   Review           2423 non-null   int64 
 8   Photos           2423 non-null   int64 
 9   Length           2423 non-null   int64 
 10  y                2423 non-null   int64 
dtypes: int64(7), object(4)
memory usage: 227.2+ KB


In [36]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 12113 entries, 0 to 12112
Data columns (total 11 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Column1          12113 non-null  int64 
 1   restaurant_name  12113 non-null  object
 2   Reviewer         12113 non-null  object
 3   comments         12113 non-null  object
 4   score            12113 non-null  int64 
 5   date             12113 non-null  object
 6   Follower         12113 non-null  int64 
 7   Review           12113 non-null  int64 
 8   Photos           12113 non-null  int64 
 9   Length           12113 non-null  int64 
 10  y                12113 non-null  int64 
dtypes: int64(7), object(4)
memory usage: 1.1+ MB


In [37]:
#Number of Permutations
permutations = 128

#Number of Recommendations to return
num_recommendations = 5

In [38]:
def preprocess(text):
    tokens = word_tokenize(normalize(text))
    #tokens = word_tokenize(text)
    
    return tokens


In [39]:
def get_forest(data, perms):
    start_time = time.time()
 
    
    
    minhash = []
    for text in data['comments']:
        
        tokens = preprocess(text)
        
        m = MinHash(num_perm=perms)
        for s in tokens:
            m.update(s.encode('utf8'))
        minhash.append(m)
        
    forest = MinHashLSHForest(num_perm=perms)
    
    for i,m in enumerate(minhash):
        forest.add(i,m)
        
    forest.index()
    
    print('It took %s seconds to build forest.' %(time.time()-start_time))
    
    return forest

In [40]:
def predict(text, database, perms, num_results, forest):
    start_time = time.time()
    column_list = ['comments','y'] 
    # text input data to predict
    # database = df input 
    tokens = preprocess(text)
    m = MinHash(num_perm=perms)
    for s in tokens:
        m.update(s.encode('utf8'))
        
    idx_array = np.array(forest.query(m, num_results))
    print(idx_array)
    if len(idx_array) == 0:
        return None # if your query is empty, return none
    
    result = database.iloc[idx_array][column_list]
    
    
    print('It took %s seconds to query forest.' %(time.time()-start_time))
    
    return result


In [45]:
forest = get_forest(df_train, permutations)

It took 46.45643949508667 seconds to build forest.


In [46]:
df_test.head()

Column1                        restaurant_name          Reviewer  \
11617       15                           Reiwa (เรวะ)               Pim   
6943        32  อาอีซะฮ์ รสดี บางลำพู (อาอีซะฮ์ รสดี)             Alice   
2264         1                     จีจ้งหว่อ ภัตตาคาร         Mr.Stew 🍖   
6911         0  อาอีซะฮ์ รสดี บางลำพู (อาอีซะฮ์ รสดี)  N o-o M One Days   
4002        90    ทิพย์สมัย ผัดไทยประตูผี (ทิพย์สมัย)         GobGap H.   

                                                comments  score  \
11617  ร้านอาหารญี่ปุ่นที่ทำโดยคนญี่ปุ่นมันดีอย่างนี้...      5   
6943   รู้จักร้านนี้ตั้งแต่ตอนเด็กแม่พากินถิ่นบางลำภู...      5   
2264   จีจังหว่อ(วังบูรพา)ร้านอาหารเก่าแก่แห่งย่านวัง...      4   
6911   ไมได้มาย่านบางลำภูนานแสนนานเลยตั้งใจมาร้านนี้ท...      4   
4002   วันนี้มีโอกาสมาทานร้านผัดไทเจ้าเก่าเจ้าดังที่ร...      4   

                       date  Follower  Review  Photos  Length  y  
11617           6 ก.ค. 2020         0       1      11     180  1  
6943           15 พ.ค. 2016        16     147    1181     342  0  
2264           29 พ.ค. 2019       584    1604    9928     426  0  
6911   เมื่อ 3 เดือนที่แล้ว        66     782    5194     386  0  
4002           10 ก.ค. 2017      5710    1511   11309     296  0

In [49]:
df_test['comments'].count()

2423

In [56]:
num_recommendations = 10

#for i in range(df_test['comments'].count()):
list_index_test = df_test.index.tolist()


tmp_dat = []

df_allresult = pd.DataFrame(columns=['comments','y'])
#df_result_sim = pd.DataFrame(columns=['test_comment','sim'])



#for i in list_index_test[12:20]:
for i in list_index_test:    
    result = predict(df_test['comments'][i], df_train, permutations, num_recommendations, forest)
    if result is None :
        continue
    else :
        result_tmp = result.assign(test_comment = (df_test['comments'][i]))
        df_allresult = df_allresult.append(result_tmp)
    
    #print('\n Top Recommendation(s) is(are) \n', result)
    df_output = pd.DataFrame(result,columns= ['comments','y'])
    list_index = df_output.index.tolist()
    list_score = []
    list_y = []
    
    
    #title1 = df_test['comments'][0]

    #tokens1 = preprocess(title)
    tokens1 = preprocess(df_test['comments'][i])
    m1 = MinHash(num_perm=128)
    m2 = MinHash(num_perm=128)



    for s in tokens1:
        m1.update(s.encode('utf8'))



    for j in list_index:
        tokens2 = preprocess(df_output['comments'][j])
        for s in tokens2:
            m2.update(s.encode('utf8'))
        print(m1.jaccard(m2))
        list_score.append(m1.jaccard(m2))
        list_y.append(df_output['y'][j])
    
    finalresult = sum(map(lambda Xi, Yi: Xi * Yi, list_score, list_y)) /sum(list_score)
    print(df_test['comments'][i] , "\nThe result is ", finalresult)
    tmp_dat.append([df_test['comments'][i],finalresult,df_test['y'][i]])
    
                
    #df_result_sim = df_result_sim.append(df_test['comments'][i],finalresult)

df_result_sim = pd.DataFrame(tmp_dat,columns=['test_comment','sim','y_true'])


    

[4384 4549 9479 2218 5388 1519 1393 5046 8438 7423]
It took 0.012517213821411133 seconds to query forest.
0.1796875
0.171875
0.140625
0.140625
0.125
0.1171875
0.1015625
0.09375
0.078125
0.0546875
ร้านอาหารญี่ปุ่นที่ทำโดยคนญี่ปุ่นมันดีอย่างนี้นี่เองคือสดมากๆๆอร่อยถูกปากคนไทยด้วยเมนูเยอะมากกราคาก็น่ารักที่สำคัญมีที่จอดรถตรงข้ามร้านเลยคือสะดวกมากกไม่ต้องไปไหนไกลแล้ว 
The result is  0.18181818181818182
[3301 2054 4044 4398  302 6864 2291 8051 2005 9427]
It took 0.013014078140258789 seconds to query forest.
0.1484375
0.109375
0.1015625
0.09375
0.109375
0.1015625
0.09375
0.09375
0.09375
0.0859375
รู้จักร้านนี้ตั้งแต่ตอนเด็กแม่พากินถิ่นบางลำภูชอบเนื้ออยู่แล้วร้านนี้ก๋วยเตี๋ยวเนื้ออร่อยถ้ามาตอนกลางวันคนเยอะทำใจนะ

มีลูกชิ้นปิ้งหน้าร้านตอนนี้ย้ายมาปิ้งด้านในละชอบแบบมะก่อนมากกว่าลูกใหญ่ดี
หลังๆมาไม่มีเนื้อสะเต๊ะแล้วไม่รู้เลิกทำยัง

ก๋วยเตี๋ยวอร่อยทั้งน้ำทั้งแห้งต้องกินทั้งสองแบบ
ซุปหางร้านนี้ราคาไม่แพงเท่าร้านอื่นคุ้มค่ามาก😊 
The result is  0.26515151515151514
[7968 5922 1385 8172 8173 5838 4303

0.2109375
0.1796875
0.1484375
0.1328125
0.1328125
0.140625
0.1328125
0.1015625
0.1015625
เป็นนิยมแก่คนต่างชาติจริงๆกับผัดไทเจ้านี้เพื่อนเกาหลีอยากมาเลยพาไปร้านไม่มีที่จอดต้องไปจอดเส้นข้างวัดแล้วเดินมาสั่งวันนั้นไป17.00เลยรอคิวไม่นานมีเซ็ทๆให้เลือกผมเลือกกุ้งสดรสชาติก็อร่อยแต่ก็ยังไม่ที่สุดยังขาดอะไรแต่ก็อธิบายไม่ถูกส่วนของดีอีกอันคือน้ำส้มแต่แพงอิ๊บอ๋ายยก็อย่างว่าของอร่อยก็เลยลองมาทานดู 
The result is  0.08629441624365482
[6656 4133 2410 4082 1587 2359 4440 5145 7418 9308]
It took 0.006995201110839844 seconds to query forest.
0.1484375
0.1484375
0.125
0.078125
0.0546875
0.046875
0.0390625
0.046875
0.0390625
0.0390625
บรรยากาศดีเหมาะพาครอบครัวไปทานข้าวอากาศดีวิวดีมองไปเห็นทะเลที่จอดรถกว้างแต่ทางเข้าเป็นซอยค่อนข้างแคบเข้าไปไม่ลึกมากห่างจะตัวเมืองพัทยาโดยรวมคุ้มค่ามากส่วนตัวมารอบที่2แล้ว🍃🌤🏝 
The result is  0.10204081632653061
[3426 4195 7270 7175 1290 3083 2346 2609 6578 4952]
It took 0.008991718292236328 seconds to query forest.
0.1171875
0.171875
0.1640625
0.1640625
0.125
0.1171875
0.09

0.046875
0.046875
อยากแวะมาทานผัดไทยชื่อดังขึ้นชื่อรางวัลเขาเพียบจริงคิวยาวมากๆต่างชาติมาทานแยะราคาแอบแรงสักนิดมีเซอวิสต์ชาร์ทด้วยง่ายังไงไงก็ถือว่าเป็นประสบการณ์การกินอีกที่นึงเอาไว้เม้าได้เค้ามาแว้ววววว 
The result is  0.1485148514851485
[7616 8450 1698 4528 5523 6965 7446  601 7642 7742]
It took 0.00900721549987793 seconds to query forest.
0.1171875
0.078125
0.0703125
0.0703125
0.078125
0.0703125
0.0703125
0.0703125
0.0703125
0.0703125
​ขาหมูเจริญแสงสีลม​ร้านขายขาหมูคนเยอะมาก​ต้องรีบไปจับจองโต๊๊ะก่อนเที่ยง​ไม่งั้นไม่ได้ทาน​เจ้าของร้านอาเฮียนิสัยน่ารัก​ถึงร้านจะวุ่นวานแต่ก็ยังมาอธิบายเรื่องของคากิและข้อคากิให้พวกเราเข้าใจมากขึ้น​จุดเด่นนอกจากขาหมูแล้วก็มีน้ำจิ้มที่รสชาติกลมกล่อม​ฟินเบาๆ​จะมีเมนูเนื้อล้วน​หรือเนื้อหนัง​หากจะสั่งกลับบ้านต้องรีบมาเพราะจะไม่ได้​จ้า​ 
The result is  0.7244897959183674
[7681 3332 9158 6312 4072 4237 9326 5585 4855 5823]
It took 0.015022516250610352 seconds to query forest.
0.2109375
0.2421875
0.234375
0.21875
0.1875
0.1875
0.1640625
0.1640625
0.15625
0.148

0.1328125
0.2265625
0.2421875
0.2109375
0.2265625
0.21875
0.2109375
0.2109375
0.1953125
0.171875
หลังจากไม่ได้ไปทานที่ร้านนานมากเนื่องจากเวลาไม่ได้แถมคิวย๊าวยาวจึงต้องโบกมือลากันไปจนรอบนี้สั่งผ่านLineManก็ได้ทานสมใจค่าบริการหลังหักส่วนลดจากโค๊ด80บาทแล้วยังต้องจ่ายอีก128บาท😥

เมนูที่สั่งทานเอง
-ผัดไทยเส้นจันท์มันกุ้งกุ้งสดห่อไข่ราคา90บาทแพคเกจช่างต่างจากผัดไทยธรรมดา(ราคา60บาท)ซะเหลือเกินเส้นจันท์เหนียวนุ่มผัดกับมันกุ้งทั่วๆเส้นไม่แฉะเกินไปไม่ร้อนและสวยงามเท่าทานที่ร้านห่อไข่บางๆได้กุ้งสด2ตัวเนื้อสดเด้งตัวใหญ่พอสมควรนะแค่บีบมะนาวทานกับถั่วงอกใบกุยช่ายก็พอแล้ว

เมนูอื่นไม่ได้ทานเองและขอรวบรูปภาพรอบก่อนที่เคยทานใส่ไปด้วย

#รีวิวที่1592
-----------------------------
ความชอบของแต่ละคนไม่เหมือนกันรีวิวนี้จึงเป็นเพียงการแสดงความคิดเห็นส่วนบุคคลในเมนูที่สั่งของวันที่ทานณร้านนี้เท่านั้น 
The result is  0.0
[6043 4773 4234 8747 4427 6514 3030 7675 1977 4667]
It took 0.022005319595336914 seconds to query forest.
0.2265625
0.25
0.25
0.203125
0.1796875
0.1484375
0.1484375
0.1328125
0.125
0.1171875
ว

0.171875
0.15625
0.1640625
0.1640625
0.1640625
0.1796875
0.203125
0.2109375
ออกตัวแรงก่อนว่าเอาจริงจากเดิมไม่เคยรู้จักร้านนี้เลยอ่ะ^^"มารู้จักก็เพราะคนที่ทำงานที่บังเอิญอยู่แถวนี้แล้วเค้าพูดกันว่าต้องลองๆต้องมาลองซักครั้งค่ะเราก็มาลองแต่ตามหัวหน้ามานะที่ไหนฟรีเราก็ไปไม่อิดออดอยู่แล้วฮ่าาาาา

ร้านCopperที่เรามาลองอยู่ที่คอมมูนิตี้TheSenseปิ่นเกล้าหาไม่ยากอยู่ติดกับเซ็นทรัลปิ่นเกล้าเลยชนิดที่เดินมาจากเซ็นปิ่นยังได้แต่จะเดินมาทำไมเล่าในเมื่อTheSenseก็มีที่จอดรถฮ่าาาาซึ่งตอนนี้เค้าเหมือนจะเริ่มเก็บค่าที่จอดแล้วนะคะทานเสร็จอิ่มแล้วอย่าลืมแสตมป์บัตรจอดรถกันด้วยนะคะ^^

สไตล์ของCopperเนี่ยจะเป็นแนวInternationalมีอาหารให้เลือกทานหลายสัญชาตินิยามง่ายๆก็คืออยากทานอะไรต้องได้ทานนั่นแหละซึ่งตอนแรกเราก็นึกภาพไม่ออกนะจนมาทานนี่แหละเชื่อแล้วว่ามีทุกอย่างที่อยากทานจริงๆแม้กระทั่งก๋วยเตี๋ยวและส้มตำรสชาติอาจจะแบบไม่ถึงขนาดร้านประจำแต่ก็ไม่อ่อนแอนะ

เราขอรีวิวแบบรวมๆเลยละกันบุฟเฟ่ต์ที่นี่เค้าจะมีการแบ่งโซนคล้ายๆกับที่อื่นเลยมีเป็นโซนอาหารทะเลแบบoniceและแบบอุ่นร้อนแน่นอนว่าโซนที่ป๊อปที่สุดคือหอยนางรมและหอย

...

0.234375
0.2109375
0.1953125
0.2109375
0.1875
0.140625
0.15625
0.15625
0.15625
ปชวนชิม:Paradaicraftedchocolate-ช็อคโกเลตไทยไม่แพ้ชาติใดในโลกการันตีด้วย2รางวัลinternationalchocolateaward2018

ในเพลานี้ข่าวช็อคโกเลตที่ดังสุดก็ของพี่ไทยร้านนี้ละปลื้มใจจังทำไมเราไม่รู้ๆมารู้กันเถอะ
ร้านเขาอยู่ถนนตะนาวสี่แยกคอกวัวจอดรถลำบากอยากกินใช่มั้ยพี่linemanช่วยได้
อาหาร-สั่ง2อย่างsignaturehotchocolateกับbonbonchocหลากไส้สั่งมาเป็นboxset8ลูกต่อกล่องเน้นหลายหลากอะประกอบด้วยรัมเรซิ่น,ส้มสายน้ำผึ้ง,ราสเบอรี่กระเจี๊ยบ,ชาไทย,ฮาเซลนัทมาลิบู,passionblacksasemeอย่าถามว่าอันไหนเป็นอันไหนรู้แต่ว่าชอบรสผลไม้ทุกอันโดยเฉพาะที่มีรสเปรี้ยวที่สุดน่าจะส้มกับราสเบอรี่กระเจี๊ยบกินแล้วมันฟินนนม๊ากกมันเข้ากันกับช็อคกรอบกรุบด้านนอกและนุ่มด้านในมีชั้นผลไม้ร่วมด้วยช็อคหอมมันขมนิดๆไม่หวานจัดชอบมากนานๆจะเจอช็อคไม่หวานเสียทีส่วนhotchocเข้มข้นกลางๆอร่อยดีให้bonbon9.5ช็อคร้อน8.5
ราคา-สิริรวมทั้งหมด720บาทพี่linemanราคาสูงนิดแต่ของเขาดีอะให้9 
The result is  0.40350877192982454
[5858 6563 6660 5417  496 7985 2930 2486 4502 6840]
It

0.1015625
0.1015625
0.1015625
0.078125
0.0703125
0.0703125
ความอร่อยของที่นี้คนเยอะมากถึงขนาดต้องขยายที่จอดรถตรงด้านหลังของร้านเพิ่มเติมไปอีกเมนูที่อยากแนะนำคงหนีไม่พ้นเป็ดพะโล้ครับเพราะขนาดชื่อร้านยังบอกเลยครับการบริหารจัดการของทางร้านก็ดีมากครับถึงคนเยอะแต่อาหารไม่ช้าเลย 
The result is  0.5597014925373134
[ 359 7386 2283 1324 2990 9684 7188 9112 2810 3678]
It took 0.007002115249633789 seconds to query forest.
0.140625
0.1484375
0.1796875
0.1875
0.171875
0.15625
0.1484375
0.140625
0.125
0.140625
ตามนั้นครับร้านสวนผักโอ้กะจู๋ได้ยินชื่อมานานเมื่อมีโอกาสมาเมืองเชียงใหม่เลยต้องขอลองสักที

เริ่มต้นด้วยสลัดผักซึ่งได้ผักที่สดใหม่มากได้ความกรอบกันเลยทีเดียวจานใหญ่จนเอาจริงๆก็เรียกได้ว่าสามารถทานสลัดจนอิ่มได้

สเต๊กปลาแอลมอนด์เอาชิ้นเนื้อปลาไปชุบเมล็ดแอลมอนด์แล้วทอดรสชาติปลาหมักไว้ใช้ได้ดีเลยทีเดียว

ความคุ้มค่าต่อราคา5/5
รสชาติ4.5/5
ความสะอาด5/5
บรรยากาศร้าน5/5
บริการ5/5

รสชาติลางเนื้อชอบลางยานะครับ 
The result is  0.2131979695431472
[8288  419 8389 9319 6120 6448 2036 8541 1789 8383]
It too

0.1875
0.1796875
0.171875
0.1640625
0.1640625
0.1640625
0.1640625
0.1640625
0.140625
ร้านนี้อยู่ย่านทองหล่อเพื่อนชวนไปกินบุฟเฟ่ต์อร่อยๆเลยตามเค้าไปตอนแรกที่ไปดูทางเข้าแล้วไม่น่าเข้ามาเลยซอยเล้กๆแคบๆซอยอย่างงี้จะมีร้านอาหารอร่อยๆหรอแต่เมื่อเข้าไปภายในร้านแล้วบรรยากาศโอเคดีหลังจากสั่งรายการอาหารพวกหมูหมักสันคอหมูหมูสานชั้นคอหมูกับเครื่องเคียงต่างๆย่างๆไปก็ได้กลิ่นหมอของซอสหมักพอได้ลิ้มรสหมูที่ย่างจากเตามาร้อนๆอยากบอกว่าอร่อยล้ำจริงๆโดยเฉพาะหมูสามชั้นชอบมากๆแต่หมูชิ้นจะยาวมากจนต้องใช้กรรไกรตัดให้เป็นชิ้นพอดีคำก่อนทานหรือใครจะทานที่เดียวชิ้นใหญ่ๆก็ไม่ว่ากันราคาต่อหัว290บาทเน็ตแล้วสนใจลองเข้าไปทานกันได้ค่ะร้านปิดทุกวัน11.00-22.00นแต่ครัวปิด21.00นนะคะ 
The result is  0.4027777777777778
[4768  992 7873  289 4325 1226 1428 3127 9307 7039]
It took 0.00500178337097168 seconds to query forest.
0.140625
0.140625
0.15625
0.1328125
0.0859375
0.078125
0.078125
0.078125
0.078125
0.0703125
ชูชิที่ชื่อแจคกี้(จัดวางเป็นรูปหนอน)อร่อยดี
ใครมีโอกาสไปต้องลองเมนูนี้เลยนะ
จริงๆแล้วก็อร่อยทุกเมนูลยแหละ
วันนั่นฟ

0.125
0.1171875
0.1171875
0.09375
0.0859375
0.0859375
0.078125
เปิดเห็นรูปก๋วยเตี๋ยวหมูแล้วก็นึกถึงร้านรุ่งเรืองก๋วยเตี๋ยวขึ้นมามิรอช้ารีบบึ่งรถมุ่งหน้าตรงสู่สุขุมวิท26เลยทีเดียว🍜

จัดไปเบาๆกับเส้นเล็กหมูต้มยำกับเส้นหมี่หมูน้ำใสคือบั๊บกินเท่าไรกินเมื่อไรกินตอนไหนก็ไม่เคยผิดหวังเลยจริงๆหมูชิ้นโตเคี้ยวอร่อยน้ำซุปกลมกล่อมสั่งปลากรอบมากินด้วยอีกสักจานคือดีงามอย่าบอกใคร😋😊 
The result is  0.07857142857142857
[1446 3185 6994 1716 5013 3478 2775 5592 6233 3354]
It took 0.006001710891723633 seconds to query forest.
0.1875
0.140625
0.09375
0.078125
0.078125
0.078125
0.0625
0.0546875
0.0625
0.0625
ผากมาเยือนเจียงใหม่จะไม่กินอาหารเหนือกันได้จะใด
ต้องมาแวะชิมกันเน้อ

หนึ่งในฮ้านที่เป็นที่นิยมของนักท่องเที่ยวติดอันดับ10ร้านต้องกินในเชียงใหม่เห็นจะพลาดไม่ได้กับร้านนี้

ต๋องเต็มโต้ะ

เป็นร้านอาหารเหนืออาหารพื้นบ้านค่ะ
ร้านอยู่ในซอยนิมมานกดเนวิเกเตอร์มาเลยรู้จักอยู่แร้ว
ผากมาช่วงเย็นๆค่ำๆต้องจองโต้ะกันหน่อยนะคะ
ลูกค้าแน่นมากอาจอดกินเอาได้

เมนูอาหารก็เน้นเป็นอาหารเหนือค่ะ
อาหารภา... 
The result is  0.1

0.0625
0.0625
หมูแดงเน้นๆไข่ยางมะตูมฟองใหญ่ๆรสชาติจากรุ่นพ่อสู่รุ่นลูกไม่เคยเปลี่ยน

วันนี้ได้ทานข้าวหมูแดงหมูกรอบใส่กุนเชียงพร้อมไข่ยางมะตูมแบบtakeawayอร่อยมากโปรตีนล้วนๆปริมาณข้าวกำลังดีไม่มากไปไม่น้อยไป

แนะนำสำหรับแวะทานที่เยาวราช

ปกติสั่งกลับบ้านเค้าจะใส่ห่อให้แต่นี่เราเอามาเทใส่กล่องอีกที 
The result is  0.05333333333333334
[1057 1609 7209 5450 6796 1460 9525 6420 2105  158]
It took 0.0059947967529296875 seconds to query forest.
0.0859375
0.0859375
0.1171875
0.0859375
0.046875
0.046875
0.046875
0.046875
0.046875
0.046875
ข้าวหมูแดงสีมรกต: &nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;ไม่ต้องสงสัยว่าข้าวหมูแดงทำไมเป็นสีเขียว..จริงๆแล้วคือนามสกุลเจ้าของร้านมีทีเด็ดตรงที่ทุกอย่างล้วนผ่านกรรมวิธีการย่างย่างมาตลอดสี่สิบกว่าปีร้านอยู่ในตรอกโรงหมูตรงข้ามวัดไตรมิตรขายเวลา11.30น.-22.00น 
The result is  0.20238095238095238
[ 993 4353 6888 4492 1868 4761 7575 1177 1851 5887]
It took 0.004998922348022461 seconds to query forest.
0.1328125
0.125
0.1328125
0.1328125
0.125
0.125
0.1171875
0.

In [57]:
df_result_sim

test_comment       sim  y_true
0     ร้านอาหารญี่ปุ่นที่ทำโดยคนญี่ปุ่นมันดีอย่างนี้...  0.181818       1
1     รู้จักร้านนี้ตั้งแต่ตอนเด็กแม่พากินถิ่นบางลำภู...  0.265152       0
2     จีจังหว่อ(วังบูรพา)ร้านอาหารเก่าแก่แห่งย่านวัง...  0.075188       0
3     ไมได้มาย่านบางลำภูนานแสนนานเลยตั้งใจมาร้านนี้ท...  0.100000       0
4     วันนี้มีโอกาสมาทานร้านผัดไทเจ้าเก่าเจ้าดังที่ร...  0.252632       0
...                                                 ...       ...     ...
2414  ข้าวหมูแดงสีมรกต:
&nbsp;&nbsp;&nbsp;&nbsp;&nbs...  0.202381       1
2415  พูลสินภัตราคารเป็นร้านอาหารจีนเก่าแก่ร้านนึงจึ...  0.114094       0
2416  ร้านอร่อยช่วงสงกรานต์บรรยากาศริมน้ำคนไม่แน่นมา...  0.136842       0
2417  🍫PARADAiภราดัยCraftedChocolate&amp;Cafe🍫คาเฟ่น...  0.491525       1
2418  อาหารพื้นเมืองนิมมาน13\n\nเจอร้านนี้โดยบังเอิญ...  0.243902       0

[2419 rows x 3 columns]

In [58]:
# export to csv file
df_result_sim.to_csv('pre_result.csv',encoding='utf-8')